In [107]:
# start with the setup
import pandas as pd
import altair as alt
import numpy as np
import pprint
from vega_datasets import data

In [139]:
#load data 
df = pd.read_csv('economics.csv')
df2 = pd.read_csv('educationall.csv')
df3 = pd.read_csv('educationrlc.csv')
df['id'] = pd.to_numeric(df['id'])
df

Unnamed: 0                County  state  countycode            county  \
0              1  Abbeville County, SC     45           1  Abbeville County   
1              2     Acadia Parish, LA     22           1     Acadia Parish   
2              3   Accomack County, VA     51           1   Accomack County   
3              4        Ada County, ID     16           1        Ada County   
4              5      Adair County, IA     19           1      Adair County   
...          ...                   ...    ...         ...               ...   
3123        3124       Yuma County, AZ      4          27       Yuma County   
3124        3125       Yuma County, CO      8         125       Yuma County   
3125        3126     Zapata County, TX     48         505     Zapata County   
3126        3127     Zavala County, TX     48         507     Zavala County   
3127        3128    Ziebach County, SD     46         137    Ziebach County   

      propertyrate  Unemployrate                      County.State  \
0             19.1           6.8  Abbeville County, South Carolina   
1             23.7           6.8          Acadia Parish, Louisiana   
2             20.4           5.4         Accomack County, Virginia   
3             11.7           3.4                 Ada County, Idaho   
4             11.9           3.2                Adair County, Iowa   
...            ...           ...                               ...   
3123          21.1          21.8              Yuma County, Arizona   
3124          14.1           2.5             Yuma County, Colorado   
3125          30.9           7.7              Zapata County, Texas   
3126          32.0          11.3              Zavala County, Texas   
3127          47.1           5.0      Ziebach County, South Dakota   

      Population  Median.household.income State.Code           State     Area  \
0          24997                  34799.0         SC  South Carolina    South   
1          62163                  37649.0         LA       Louisiana    South   
2          33115                  39412.0         VA        Virginia    South   
3         417501                  56356.0         ID           Idaho     West   
4           7426                  46526.0         IA            Iowa  Midwest   
...          ...                      ...        ...             ...      ...   
3123      202987                  40743.0         AZ         Arizona     West   
3124       10185                  43105.0         CO        Colorado     West   
3125       14308                  32162.0         TX           Texas    South   
3126       12060                  26672.0         TX           Texas    South   
3127        2833                  35119.0         SD    South Dakota  Midwest   

         id  medianIncome  
0     45001       34799.0  
1     22001       37649.0  
2     51001       39412.0  
3     16001       56356.0  
4     19001       46526.0  
...     ...           ...  
3123   4027       40743.0  
3124   8125       43105.0  
3125  48505       32162.0  
3126  48507       26672.0  
3127  46137       35119.0  

[3128 rows x 15 columns]

In [170]:
base = alt.Chart(df).properties(height = 300, width = 300)
selection = alt.selection_multi(fields=['Area'], bind='legend')
brush1 = alt.selection_interval(encodings = ['x','y'])
brush2 = alt.selection_interval(encodings=["x"])
opacity=alt.condition(selection, alt.value(0.4), alt.value(0.05))

redlake = pd.DataFrame({
    'x': [6],
    'y': [9.7]
})

plot = base.mark_point(opacity=0.4,filled = True,size = 10).encode(
    alt.X('Unemployrate:Q'),
    alt.Y('propertyrate:Q'),
    color=alt.condition(brush1, 'Area:N', alt.value('lightgray')),
    opacity=opacity,
    tooltip = "County:N",
).add_selection(brush1).add_selection(selection).transform_filter(brush2)


point = alt.Chart(redlake).mark_point(color='black', size = 80,filled = True).encode(
    alt.X('x:Q'),
    alt.Y('y:Q')
)

histogram = base.mark_bar().encode(
    alt.X('medianIncome:Q',
         bin=alt.Bin(step=5000)),
    alt.Y('count(medianIncome):Q'),
    color = 'Area:N',
    tooltip= 'Area:N'
).add_selection(brush2).transform_filter(selection).transform_filter(brush1)

line1 = alt.Chart(pd.DataFrame({'x': [50332],'y':['Red lake county']})).mark_rule(color = 'red',size = 3).encode(
    x='x')

line2 = base.mark_rule(color = 'black',size = 3).encode(
    x = 'median(medianIncome):Q',
)

line3 = base.mark_rule(color = 'black',size = 2).encode(
    x = 'median(Unemployrate):Q')

line4 = base.mark_rule(color = 'black',size = 2).encode(
    y = 'median(propertyrate):Q')

counties = alt.topo_feature(data.us_10m.url, 'counties')

states = alt.topo_feature(data.us_10m.url, 'states')
source = data.income.url




base = alt.Chart(counties).mark_geoshape().encode(
    color='medianIncome:Q',
).transform_filter(selection).transform_lookup(
    lookup='id',
    from_=alt.LookupData(df, 'id', ['medianIncome']),
).project(
    type='albersUsa'
)


((histogram+line1+line2) | (plot+point+line3+line4)) & map


alt.VConcatChart(...)

In [151]:
base = alt.Chart(df).properties(height = 300, width = 300)
selection = alt.selection_multi(fields=['State'], bind='legend')
brush2 = alt.selection(type='interval')
selection2 = alt.selection_interval(bind='scales')

redlake = pd.DataFrame({
    'x': [6],
    'y': [9.7]
})

plot_in = base.mark_point(opacity=0.6,filled = True).encode(
    alt.X('Unemployrate:Q'),
    alt.Y('propertyrate:Q'),
    color = "Area:N",
    tooltip = "County:N",
    opacity=alt.condition(selection, alt.value(0.6), alt.value(0.05)),    
).add_selection(selection).add_selection(selection2).transform_filter(brush2)

point = alt.Chart(redlake).mark_point(color='black', size = 120,filled = True).encode(
    alt.X('x:Q'),
    alt.Y('y:Q')
)

histogram = base.mark_bar().encode(
    alt.X('medianIncome:Q',
         bin=alt.Bin(step=5000)),
    alt.Y('count()'),
    color = 'Area:N',
    tooltip= 'Area:N'
).add_selection(brush2).transform_filter(selection2).transform_filter(selection)

line = alt.Chart(pd.DataFrame({'x': [50332],'y':['Red lake county']})).mark_rule(color = 'black',size = 3).encode(
    x='x',
    tooltip = 'y:N'
)
(histogram+line)  | (plot_in + point).interactive()


alt.HConcatChart(...)

In [78]:
education_long = pd.wide_to_long(df2, ["low", "high"], i=['FIPS Code','State','Area name'], j="Year")
education_long = education_long.reset_index()
df4 = df3.pivot(index='Year', columns='education', values='Percent')
educationrcl = df4.reset_index()


In [133]:
alt.data_transformers.disable_max_rows()
pts = alt.selection(type="single", encodings=['x'])
selection = alt.selection_single(fields=['Year'])
color_scale = alt.Scale(
    domain=("Less than high school","High school","some college","college or higher"),
    range=("#c30d24", "#f3a583", "#cccccc", "#94c6da")
)

base2 = alt.Chart(education_long)
rect = base2.mark_rect().encode(
    alt.X('low:Q', bin=True , sort = '-x'),
    alt.Y('high:Q', bin=True),
    alt.Color('count()',
        scale=alt.Scale(scheme='greenblue'),
        legend=alt.Legend(title='Total Records')
)).transform_filter(selection).properties(
    width=300,
    height=200
)



circ2 = alt.Chart(pd.DataFrame({'x': [60,45.4,35.7,21.2,7.4],'y':[6.3,7.0,9.3,10.7,16.2],'Year':[1970,1980,1990,2000,2015]})).mark_point(filled = True,size = 300).encode(
    x='x',
    y = 'y',
    color = alt.Color('Year:N',scale=alt.Scale(scheme='reds'))
).transform_filter(selection)


bar = alt.Chart(df3).mark_bar().encode(
    x=alt.X('Year:N'),
    y=alt.Y('Percent:Q',scale = alt.Scale(domain = (0,100))),
    color=alt.Color('education:N'),
    opacity = alt.condition(selection, alt.value(1), alt.value(0.3))
).add_selection(selection).properties(
    width=200,
    height=200
)



(bar |rect + circ2).resolve_legend(
    color="independent",
    size="independent"
)

alt.HConcatChart(...)

In [171]:
color_scale = alt.Scale(
    domain=("Less than high school","High school","some college","college or higher"),
    range=("#c30d24", "#f3a583", "#cccccc", "#94c6da")
)
alt.Chart(df3).mark_bar().encode(
    x='Year:N',
    y=alt.Y('Percent:Q'),
    color=alt.Color('education:N',
    scale=color_scale))

alt.Chart(...)